

# コマンドラインインターフェース

.. csv-table::
   :header: コマンド, 説明
   :widths: 20, 40
   :escape: \

    ask, 新規トライアルを作成しパラメータを提案
    best-trial, 最適トライアルを表示
    best-trials, Pareto フロントに位置するトライアル一覧を表示
    create-study, 新規スタディを作成
    delete-study, 指定スタディを削除
    storage upgrade, ストレージのスキーマをアップグレード
    studies, スタディ一覧を表示
    study set-user-attr, スタディにユーザ属性を設定
    tell, ask コマンドで作成されたトライアルを終了
    trials, トライアル一覧を表示

Optuna は上記の表に示すコマンドラインインターフェースを提供します。

IPython シェルではなく、Python スクリプトファイルを書いている状況を想定します。
以下のようなスクリプトを書くのは全く問題ありません:


In [ ]:
import optuna


def objective(trial):
    x = trial.suggest_float("x", -10, 10)
    return (x - 2) ** 2


if __name__ == "__main__":
    study = optuna.create_study()
    study.optimize(objective, n_trials=100)
    print("Best value: {} (params: {})\n".format(study.best_value, study.best_params))

しかし、研究室で新しい薬を開発するなど、Python コードで ``objective`` を明示的に書けない場合、
対話型の方法が適しています。
Optuna CLI では、`ask_and_tell` スタイルのコマンドがこのような対話的で柔軟なインターフェースを提供します。

パラメータ ``x`` が $[-10, 10]$ の範囲にある場合の目的関数値を最小化し、
目的関数値が手作業での実験によって計算されると仮定します。
それでも以下のように最適化を実行できます。
ここでは `rdb` で説明されている ``--storage sqlite:///example.db`` は無視してください。

```bash
$ STUDY_NAME=`optuna create-study --storage sqlite:///example.db`
$ optuna ask --storage sqlite:///example.db --study-name $STUDY_NAME --sampler TPESampler \
     --search-space '{"x": {"name": "FloatDistribution", "attributes": {"step": null, "low": -10.0, "high": 10.0, "log": false}}}'


[I 2022-08-20 06:08:53,158] Asked trial 0 with parameters {'x': 2.512238141966016}.
{"number": 0, "params": {"x": 2.512238141966016}}
```
``--search-space`` オプションの引数は、
:func:`optuna.distributions.distribution_to_json` を使用して生成できます。
例えば ``optuna.distributions.distribution_to_json(optuna.distributions.FloatDistribution(-10, 10))`` です。
引数の詳細については :class:`optuna.distributions.FloatDistribution` と
:class:`optuna.distributions.IntDistribution` を参照してください。

研究室で提案されたパラメータを使用して実験を行った後、
結果を Optuna のスタディに以下のように保存します:

```bash
$ optuna tell --storage sqlite:///example.db --study-name $STUDY_NAME --trial-number 0 --values 0.7 --state complete
[I 2022-08-20 06:22:50,888] Told trial 0 with values [0.7] and state TrialState.COMPLETE.
```
